In [2]:
import pandas as pd
import numpy as np
#import html2text
import random
from os import walk
from urllib.request import urlopen  # the lib that handles the url stuff
from bs4 import BeautifulSoup

#read SP Mid cap 400 stock list
MIDCAP=pd.read_excel('D:/Study/MFE/T4/EDGAR/SP midcap 400.xlsx')


#randomly choose 40 stocks with news, from pool of 80 stocks
random.seed(0)
MIDCAP_40=MIDCAP.iloc[random.sample(range(0,MIDCAP.shape[0]),80)]
MIDCAP_40.Name=MIDCAP_40.Name.apply(lambda x: x.upper())

#read idx file
DATA_READ_FROM = "D:/Study/MFE/T4/EDGAR/Data"
FILE_LIST = []
for (dirpath, dirnames, filenames) in walk(DATA_READ_FROM):
    FILE_LIST.extend(filenames)




C:\Users\castc\Anaconda32\lib\site-packages\pandas\core\generic.py:2387: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self[name] = value


In [2]:
df=pd.DataFrame()
for file in FILE_LIST: #read file by file
    #parse table
    idx = pd.read_table(DATA_READ_FROM+'/'+file, skiprows=4,sep='|')
    idx=idx.iloc[1:,:]
    
    #select news for the 40 stocks
    idx_midcap=idx[idx['Company Name'].apply(lambda x:x in MIDCAP_40.Name.tolist())]
    df=df.append(idx_midcap)

C:\Users\castc\Anaconda32\lib\site-packages\IPython\core\interactiveshell.py:2723: DtypeWarning: Columns (0) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [59]:
df.head()

CIK      Company Name Form Type  Date Filed  \
6304  1018003  INGRAM MICRO INC      10-K  2015-02-27   
6305  1018003  INGRAM MICRO INC         4  2015-01-06   
6306  1018003  INGRAM MICRO INC         4  2015-01-06   
6307  1018003  INGRAM MICRO INC         4  2015-01-06   
6308  1018003  INGRAM MICRO INC         4  2015-01-06   

                                         Filename  
6304  edgar/data/1018003/0001018003-15-000013.txt  
6305  edgar/data/1018003/0001179110-15-000448.txt  
6306  edgar/data/1018003/0001179110-15-000449.txt  
6307  edgar/data/1018003/0001179110-15-000450.txt  
6308  edgar/data/1018003/0001179110-15-000451.txt

In [10]:
df.to_csv('D:/Study/MFE/T4/EDGAR/list_files.csv')
MIDCAP_40.to_csv('D:/Study/MFE/T4/EDGAR/list_40.csv')
df['Form Type'].value_counts()

4             3848
8-K            983
SC 13G/A       377
10-Q           210
3              120
4/A            111
5              108
SC 13G          91
DEFA14A         78
DEF 14A         77
10-K            76
UPLOAD          73
425             65
CORRESP         53
11-K            48
424B5           37
SD              28
ARS             28
S-8             21
SC 13D/A        19
FWP             18
S-3ASR          18
13F-HR          14
EFFECT          13
424B2           13
8-K/A           13
424B3            9
3/A              9
POS AM           8
S-8 POS          8
              ... 
DFAN14A          4
NT 10-K          3
DEFM14A          3
DEFR14A          3
10-K/A           3
144              3
13F-HR/A         3
8-A12B           3
25               2
S-3              2
IRANNOTICE       2
PREM14A          2
DEFC14A          2
10-Q/A           2
PRRN14A          2
POSASR           2
PX14A6G          1
PREC14A          1
CT ORDER         1
RW               1
CERTNAS          1
D           

In [27]:
data = urlopen('ftp://ftp.sec.gov/'+df[df['Form Type']=='10-Q'].iloc[0].Filename).read()

In [22]:
data = urlopen('ftp://ftp.sec.gov/'+df['Filename'].iloc[1]).read()

In [28]:
soup=BeautifulSoup(data, 'html.parser')
print(soup.prettify())

<sec-document>
 0001564590-15-001408.txt : 20150306
 <sec-header>
  0001564590-15-001408.hdr.sgml : 20150306
  <acceptance-datetime>
   20150306171405
ACCESSION NUMBER:		0001564590-15-001408
CONFORMED SUBMISSION TYPE:	10-Q
PUBLIC DOCUMENT COUNT:		14
CONFORMED PERIOD OF REPORT:	20150130
FILED AS OF DATE:		20150306
DATE AS OF CHANGE:		20150306

FILER:

	COMPANY DATA:	
		COMPANY CONFORMED NAME:			ESTERLINE TECHNOLOGIES CORP
		CENTRAL INDEX KEY:			0000033619
		STANDARD INDUSTRIAL CLASSIFICATION:	INDUSTRIAL INSTRUMENTS FOR MEASUREMENT, DISPLAY, AND CONTROL [3823]
		IRS NUMBER:				132595091
		STATE OF INCORPORATION:			DE
		FISCAL YEAR END:			1002

	FILING VALUES:
		FORM TYPE:		10-Q
		SEC ACT:		1934 Act
		SEC FILE NUMBER:	001-06357
		FILM NUMBER:		15682562

	BUSINESS ADDRESS:	
		STREET 1:		500 - 108TH AVENUE NE
		STREET 2:		SUITE 1500
		CITY:			BELLEVUE
		STATE:			WA
		ZIP:			98004
		BUSINESS PHONE:		4254539400

	MAIL ADDRESS:	
		STREET 1:		500 - 108TH AVENUE NE
		STREET 2:		SUITE 1500
		CITY

In [29]:
text=soup.body.get_text()
text

"\n\xa0\nUNITED STATES\nSECURITIES AND EXCHANGE COMMISSION\nWASHINGTON, D.C.\xa020549\n\xa0\nFORM\xa010-Q\nþ QUARTERLY REPORT PURSUANT TO SECTION\xa013 OR 15(d) OF THE SECURITIES EXCHANGE ACT OF 1934\nFor the quarterly period ended January\xa030,\xa02015.\nOR\n¨ TRANSITION REPORT PURSUANT TO SECTION\xa013 OR 15(d) OF THE SECURITIES EXCHANGE ACT OF 1934\nFor the transition period from \xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0 to \xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\nCommission\xa0file\xa0number\xa01-6357\n\xa0\n\n\xa0\nESTERLINE TECHNOLOGIES CORPORATION\n(Exact name of registrant as specified in its charter)\n\xa0\n\n\n\n\nDelaware\n\n\xa0\n\n13-2595091\n\n\n\n(State or other Jurisdiction\n\n\xa0\n\n(I.R.S. Employer\n\n\n\nof incorporation or organization)\n\n\xa0\n\nIdentification No.)\n\n\n500 108th Avenue N.E., Bellevue, Washington 98004\n(Address of principal executive offices)(Zip Code)\nRegistrant’s

In [3]:
df=pd.read_csv('D:/Study/MFE/T4/EDGAR/list_files.csv')
#df2=df[df['Form Type'].apply(lambda x:x in ['4','8-K','SC 13G/A','10-K','10-Q'])]
df2=df[df['Form Type']=='8-K']
df2['Text']=pd.Series(index=df2.index)
df2.shape

C:\Users\castc\Anaconda32\lib\site-packages\ipykernel\__main__.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


(983, 7)

In [5]:
counter=0
for x, row in df2.iterrows():
    try:
        data = urlopen('ftp://ftp.sec.gov/'+row['Filename']).read()
        soup=BeautifulSoup(data, 'html.parser')
        if(row['Form Type']=='4'):
            df2.loc[x,'Text']=soup.footnotes.get_text()
        elif(row['Form Type']=='8-K'):
            df2.loc[x,'Text']=soup.body.get_text()
        elif(row['Form Type']=='SC 13G/A'):
            df2.loc[x,'Text']==soup.document.get_text()
        elif(row['Form Type']=='10-K' or row['Form Type']=='10-Q'):
            text=soup.body.get_text()
            beg=text.upper().find('MANAGEMENT’S DISCUSSION AND ANALYSIS OF FINANCIAL CONDITION AND RESULTS OF OPERATIONS',10000)
            end=text.upper().find('QUANTITATIVE AND QUALITATIVE DISCLOSURES ABOUT MARKET RISK',10000)
            df2.loc[x,'Text']=text[beg:end]
        else:
            continue    

    except:
        pass
    
    if (counter%100==0):
        print (counter, df2.shape[0]) 
    counter+=1

C:\Users\castc\Anaconda32\lib\site-packages\pandas\core\indexing.py:426: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[item] = s


0 983
100 983
200 983
300 983
400 983
500 983
600 983
700 983
800 983
900 983


In [11]:
df2.to_excel('D:/Study/MFE/T4/EDGAR/8K.xlsx')

In [12]:
df3=pd.read_excel('D:/Study/MFE/T4/EDGAR/8K.xlsx',index_col=0)

In [13]:
df3

Unnamed: 0      CIK                  Company Name Form Type  Date Filed  \
11          6315  1018003              INGRAM MICRO INC       8-K  2015-02-26   
58          9131  1025996            KILROY REALTY CORP       8-K  2015-01-29   
59          9132  1025996            KILROY REALTY CORP       8-K  2015-02-11   
94         14012   103730    VISHAY INTERTECHNOLOGY INC       8-K  2015-02-05   
95         14013   103730    VISHAY INTERTECHNOLOGY INC       8-K  2015-02-20   
96         14014   103730    VISHAY INTERTECHNOLOGY INC       8-K  2015-03-04   
97         14015   103730    VISHAY INTERTECHNOLOGY INC       8-K  2015-03-13   
128        14428  1038074      SILICON LABORATORIES INC       8-K  2015-01-08   
129        14429  1038074      SILICON LABORATORIES INC       8-K  2015-01-30   
130        14430  1038074      SILICON LABORATORIES INC       8-K  2015-02-04   
131        14431  1038074      SILICON LABORATORIES INC       8-K  2015-02-04   
174        21493  1056696      MANHATTAN ASSOCIATES INC       8-K  2015-02-03   
206        23731  1062449        BUFFALO WILD WINGS INC       8-K  2015-02-05   
248        27964  1077771          UMPQUA HOLDINGS CORP       8-K  2015-01-28   
249        27965  1077771          UMPQUA HOLDINGS CORP       8-K  2015-02-17   
250        27966  1077771          UMPQUA HOLDINGS CORP       8-K  2015-03-16   
251        27967  1077771          UMPQUA HOLDINGS CORP       8-K  2015-03-30   
294        42609  1128928             FLOWERS FOODS INC       8-K  2015-02-12   
295        42610  1128928             FLOWERS FOODS INC       8-K  2015-02-25   
340        46566  1143068       GREAT PLAINS ENERGY INC       8-K  2015-01-02   
341        46567  1143068       GREAT PLAINS ENERGY INC       8-K  2015-02-17   
342        46568  1143068       GREAT PLAINS ENERGY INC       8-K  2015-02-25   
343        46569  1143068       GREAT PLAINS ENERGY INC       8-K  2015-03-18   
344        46570  1143068       GREAT PLAINS ENERGY INC       8-K  2015-03-30   
388        54713  1179929         MOLINA HEALTHCARE INC       8-K  2015-01-13   
389        54714  1179929         MOLINA HEALTHCARE INC       8-K  2015-02-09   
390        54715  1179929         MOLINA HEALTHCARE INC       8-K  2015-02-12   
419        80463  1265888                   NEUSTAR INC       8-K  2015-02-03   
420        80464  1265888                   NEUSTAR INC       8-K  2015-03-04   
421        80465  1265888                   NEUSTAR INC       8-K  2015-03-26   
...          ...      ...                           ...       ...         ...   
6536      186777   887936            FTI CONSULTING INC       8-K  2016-08-16   
6543      190013   903127           POST PROPERTIES INC       8-K  2016-08-02   
6544      190014   903127           POST PROPERTIES INC       8-K  2016-08-15   
6568      191052   910521          DECKERS OUTDOOR CORP       8-K  2016-07-06   
6569      191053   910521          DECKERS OUTDOOR CORP       8-K  2016-07-28   
6570      191054   910521          DECKERS OUTDOOR CORP       8-K  2016-09-16   
6579      191068   910606          REGENCY CENTERS CORP       8-K  2016-07-07   
6580      191069   910606          REGENCY CENTERS CORP       8-K  2016-07-13   
6581      191070   910606          REGENCY CENTERS CORP       8-K  2016-07-15   
6582      191071   910606          REGENCY CENTERS CORP       8-K  2016-08-03   
6597      193499   921112        LIBERTY PROPERTY TRUST       8-K  2016-07-25   
6598      193500   921112        LIBERTY PROPERTY TRUST       8-K  2016-07-26   
6599      193501   921112        LIBERTY PROPERTY TRUST       8-K  2016-09-19   
6600      193502   921112        LIBERTY PROPERTY TRUST       8-K  2016-09-23   
6638      196493   936395                    CIENA CORP       8-K  2016-08-05   
6639      196494   936395                    CIENA CORP       8-K  2016-09-01   
6646      196590   936528        WASHINGTON FEDERAL INC       8-K  2016-07-14   
6647      196591   936528        WASH